# Setup

## Imports

In [1]:
%reload_ext autoreload
%autoreload 2

import sys
from pathlib import Path 
current_path = Path().resolve()
abs_path = str(current_path.parent)
sys.path.append(abs_path)

RAW_PATH = current_path.parent / 'data' / 'raw'
OUTPUT_PATH = current_path.parent / 'data' / 'output'

import warnings
warnings.filterwarnings('ignore')

import pandas as pd
pd.set_option('display.max_columns', None)

import plotly.graph_objs as go
import plotly.plotly as py
import plotly.offline as offline
offline.init_notebook_mode(connected=True)

from h3 import h3
import folium
from pyathena import connect

EXTERNAL_LOCATION = 's3://athena-fgv/'

In [ ]:
!pip3.7 install h3

## Useful functions

## Connect With Athena

In [180]:
from pyathena import connect

conn = connect(s3_staging_dir='s3://athena-fgv/test',
               region_name='us-east-2')

In [5]:
def zip_columns(res):
    return list(zip(map(lambda x: x[0], res.description), res.fetchall()[0]))

def execute(query, conn, get_data=True):
    cursor = conn.cursor()
    res = cursor.execute(query)
    if get_data:
        data = zip_columns(res)
        cursor.close()
        return data
    else:
        cursor.close()

## Declare Variables

In [2]:
boundaries =  {'max_lon': -119.949377,
 'max_lat': 39.716694,
 'min_lon': -121.802217,
 'min_lat': 38.246918}
''

oms_region_table_name = 'osm.california_district_3'

# Get OSM slice of region

## Get region boundaries 

In [10]:
query = """SELECT 
    max(longitude) max_lon,
    max(latitude) max_lat,
    min(longitude) min_lon,
    min(latitude) min_lat
FROM pems.pems_5_minute_metadata"""

In [ ]:
data = execute(query, conn)

In [ ]:
boundaries = dict(data)

## Create OSM table of region

In [3]:
query = f"""
CREATE TABLE {oms_region_table_name}
WITH (
      external_location = '{EXTERNAL_LOCATION}osm/california_district_3/3',
      format = 'ORC')
AS SELECT *
FROM osm.planet
WHERE lat < {boundaries['max_lat']}
  AND lat > {boundaries['min_lat']}
  AND lon < {boundaries['max_lon']}
  AND lon > {boundaries['min_lon']}
  """

In [5]:
print(query)


CREATE TABLE osm.california_district_3
WITH (
      external_location = 's3://athena-fgv/osm/california_district_3/3',
      format = 'ORC')
AS SELECT *
FROM osm.planet
WHERE lat < 39.716694
  AND lat > 38.246918
  AND lon < -119.949377
  AND lon > -121.802217
  


In [88]:
execute(query, conn, get_data=False)

UnboundLocalError: local variable 'data' referenced before assignment

## Plan

1. Get hexagons around sensors
2. Get hexagons boundaries
3. Create table linking sensors to OSM data

## Get hexagons around sensors

In [11]:
query = """
SELECT 
id, MAX(latitude) latitude, MAX(longitude) longitude
FROM pems.pems_station_metadata
GROUP BY id
"""

In [12]:
sensors = pd.read_sql_query(query, conn)

In [13]:
sensors.head(2)

id   latitude   longitude
0  312387.0  38.477234 -121.425761
1  312422.0  38.494914 -121.444557

## Get hexagons around sensors

In [18]:
sensors['hexagon_8'] = sensors.apply(lambda x: h3.geo_to_h3(x['latitude'], x['longitude'], 8), axis=1)

In [20]:
for i in range(7):
    sensors[f'neigh_{i}'] = sensors.apply(lambda x: h3.k_ring(x['hexagon_8'], i), 1)


In [21]:
for i in range(7):
    print('ring: ', i, 'size: ', len(h3.k_ring('88283284d1fffff', i)) * len(sensors))

ring:  0 size:  1341
ring:  1 size:  9387
ring:  2 size:  25479
ring:  3 size:  49617
ring:  4 size:  81801
ring:  5 size:  122031
ring:  6 size:  170307


In [ ]:
25479 * 0

In [112]:
sensors.head(1)

id   latitude   longitude        hexagon_8            neigh_0  \
0  312387.0  38.477234 -121.425761  8828328683fffff  {8828328683fffff}   

                                             neigh_1  \
0  {8828328681fffff, 8828328695fffff, 882832868bf...   

                                             neigh_2  \
0  {8828328681fffff, 8828328689fffff, 8828328685f...   

                                             neigh_3  \
0  {882832869dfffff, 882832868dfffff, 882832869bf...   

                                             neigh_4  \
0  {882832869dfffff, 882832868dfffff, 882832b34df...   

                                             neigh_5  \
0  {882832b347fffff, 882832868dfffff, 882832b34df...   

                                             neigh_6  
0  {882832b347fffff, 882832848bfffff, 8828304985f...

## Get hexagons boundaries

id | latitude | longitude | neigh_level | h3_id | boundaries 

In [127]:
def hexagons_to_boundaries(h3_id):
    
    try:
        a = h3.h3_to_geo_boundary(h3_id)
    except:
        print(h3_id)
    
    lats = list(map(lambda x: x[0], a))
    lons = list(map(lambda x: x[1], a))
    
    return {
     'max_lon': max(lons),
     'max_lat': max(lats),
     'min_lon': min(lons),
     'min_lat': min(lats)}


In [120]:
def flatten_df(sensors, neigh_column):
    
    df = sensors.set_index('id')[neigh_column] \
        .apply(lambda x: pd.Series(list(x))) \
        .reset_index()
    df['neigh_level'] = neigh_column[-1]
    df = df.melt(id_vars=['id', 'neigh_level'], value_name='h3_id') \
        .drop('variable', 1) 
    df = df.merge(sensors[['id', 'latitude', 'longitude']], on='id')
    return df

In [121]:
final = pd.concat([flatten_df(sensors, neigh_column) for neigh_column in sensors.columns if neigh_column not in ['id', 'latitude', 'longitude', 'hexagon_8']])

In [129]:
final = final.dropna(subset=['h3_id'])

In [130]:
final.head()

id neigh_level            h3_id   latitude   longitude
0  312387.0           0  8828328683fffff  38.477234 -121.425761
1  312422.0           0  882832b369fffff  38.494914 -121.444557
2  312773.0           0  882832b137fffff  38.598802 -121.442169
3  313393.0           0  882832b831fffff  38.666687 -121.353756
4  313475.0           0  882832b9a5fffff  38.718633 -121.297486

In [131]:
final.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 459277 entries, 0 to 170306
Data columns (total 5 columns):
id             459277 non-null float64
neigh_level    459277 non-null object
h3_id          459277 non-null object
latitude       459277 non-null float64
longitude      459277 non-null float64
dtypes: float64(3), object(2)
memory usage: 21.0+ MB


In [251]:
final['boundaries'] = final['h3_id'].apply(hexagons_to_boundaries)
final.reset_index(drop=True, inplace=True)

In [254]:
final = final.merge(pd.DataFrame.from_records(final['boundaries']), left_index=True, right_index=True)

In [255]:
len(final)

459277

In [256]:
final.head(2)

sensor_id neigh_level            h3_id   latitude   longitude  \
0   312387.0           0  8828328683fffff  38.477234 -121.425761   
1   312422.0           0  882832b369fffff  38.494914 -121.444557   

                                          boundaries    max_lat     max_lon  \
0  {'max_lon': -121.41879813686569, 'max_lat': 38...  38.483357 -121.418798   
1  {'max_lon': -121.44102691241622, 'max_lat': 38...  38.500964 -121.441027   

     min_lat     min_lon  
0  38.473979 -121.430773  
1  38.491589 -121.453003

In [262]:
maxs = final.groupby(['sensor_id', 'neigh_level', 'latitude', 'longitude']).max()[['max_lat', 'max_lon']]
mins = final.groupby(['sensor_id', 'neigh_level', 'latitude', 'longitude']).min()[['min_lat', 'min_lon']]

In [264]:
len(maxs) == len(mins)

True

In [270]:
final = maxs.reset_index().merge(mins.reset_index(), on=['sensor_id', 'neigh_level', 'latitude', 'longitude'])

In [271]:
len(maxs)==len(final)

True

In [274]:
final.head()

sensor_id neigh_level   latitude   longitude    max_lat     max_lon  \
0   311831.0           0  38.409253 -121.484009  38.410805 -121.475572   
1   311831.0           1  38.409253 -121.484009  38.419004 -121.465029   
2   311831.0           2  38.409253 -121.484009  38.427202 -121.454486   
3   311831.0           3  38.409253 -121.484009  38.435400 -121.443941   
4   311831.0           4  38.409253 -121.484009  38.443597 -121.433396   

     min_lat     min_lon  
0  38.401425 -121.487535  
1  38.393225 -121.498076  
2  38.385025 -121.508615  
3  38.376824 -121.519153  
4  38.368623 -121.529690

## Check if it makes sense

In [275]:
blatitude, longitude = sensors['latitude'][1], sensors['longitude'][1]

m = folium.Map(
    location=[latitude, longitude],
    zoom_start=13
)

folium.Circle(location=[latitude, longitude], radius=100).add_to(m)

for i, row in final[final['sensor_id'] == 312422.0].iterrows():

    folium.Circle(location=[row['max_lat'], row['max_lon']]).add_to(m)

m

## Create table linking OSM ids, sensor_id, h3_ids by neigh_level 

id_sensor | id_osm | id_h3 | neigh_level



In [156]:
final.rename(columns={'id': 'sensor_id'}, inplace=True)

In [157]:
final.head(1)

sensor_id neigh_level            h3_id   latitude   longitude  \
0   312387.0           0  8828328683fffff  38.477234 -121.425761   

                                          boundaries  
0  {'max_lon': -121.41879813686569, 'max_lat': 38...

In [276]:
from pyathena.async_cursor import AsyncCursor
cursor = connect(s3_staging_dir='s3://athena-fgv/osm_pems/raw/oms_pems_ids', region_name='us-east-2',
               cursor_class=AsyncCursor).cursor(max_workers=10)

In [233]:
query = f"""
SELECT id as osm_id,
       {int(row['sensor_id'])} as sensor_id,
       '{row['h3_id']}' as h3_id,
       {row['neigh_level']} as neigh_level
FROM osm.california_district_3
WHERE lat < {row['max_lat']}
  AND lat > {row['min_lat']}
  AND lon < {row['max_lon']}
  AND lon > {row['min_lon']}
  """

In [229]:
from copy import deepcopy

In [239]:
len(final[final['neigh_level'].isin(['0'])])

1339

In [240]:
(13*60+44) / 1339

0.6153846153846154

In [282]:
for i, row in final.iterrows():
    query = f"""
SELECT id as osm_id,
       {int(row['sensor_id'])} as sensor_id,
       {row['neigh_level']} as neigh_level
FROM osm.california_district_3
WHERE lat < {row['max_lat']}
  AND lat > {row['min_lat']}
  AND lon < {row['max_lon']}
  AND lon > {row['min_lon']}
  """
    q = deepcopy(query)

    cursor.execute(q)

ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

...

ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

In [283]:
!aws s3 rm s3://athena-fgv/osm_pems/raw/oms_pems_ids/ --recursive --exclude '*.csv'

delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0093a87a-be10-4f9d-b15a-fd60621d584e.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/000325b2-4655-409f-baa5-873f993d046e.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/00c4abc9-96fb-434e-a1f1-beaa6d72e4c9.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/00dca4b7-d341-4804-aa9e-b79e19345b9e.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/00eace14-a383-4751-b49e-3b8284a3c017.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/00f0180e-bd80-469c-93ee-d96ca76c8803.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/00fac0c6-2119-4f6e-bc2e-7e0b6f95ad32.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/01019d3d-52c0-483b-bcad-d6166c7dda38.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/00721ec0-f408-4ca9-9e25-88f5d31a349d.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/010a7ab7-12a2-483d-b1a3-491084d5f0a8.csv.metadata


delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/05f2efea-b50c-4bb4-acaf-95230711b351.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/057f82ae-b86e-4005-805d-14abf13b2964.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/058083dd-84b0-4662-bc0b-7bfc9df1bb09.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/060a7002-24e3-439e-9cac-1b90cebf11d8.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/060324dc-1f8a-4d9b-b143-c4a369d2bae3.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/060cdc90-12cb-4075-9c35-0e7c06e22dbe.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/061ea37b-8cde-40e6-894e-ac66752cee3c.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0625fc7c-b5b1-4eb9-9a78-6381d565ec12.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/06639059-70b7-425e-a58c-025bcb519061.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/04cdb59f-f2cb-4cb7-8867-5739857625e3.csv.metadata


delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0a404c75-da1d-4e5c-8b6e-56c4ca067471.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0a565f8f-c988-4892-94c5-80dd5724c6c7.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0a6882cc-1e96-4d9f-b186-9809a9a1b36e.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0a6aad6d-dd8d-43f8-ba09-14225518694f.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0a5739f5-69d8-42cd-9715-0306e512cf40.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/09f1960c-f3a3-4e8c-92ab-264756004e2e.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0a7911e0-754c-41ef-9c72-a532a03cb355.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0aa886b2-f8b4-4f6d-b5ae-6fe56f4e4555.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0aa94d8d-4db2-462a-adf1-dea3ccfb597d.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0aac0d01-5b8d-483f-b1f1-b603f02d0cea.csv.metadata


delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0e550953-0de2-4a84-b9fb-d1ea8a95469f.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0e8a7880-ba28-40b2-800d-d06fed3e25f4.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0e553d89-4449-4156-a9e0-ea34d6184a61.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0e5fb1e8-d8d2-4ba7-97bb-88bb78e3eb53.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0e9e9bd7-5d45-4e92-8aee-dde38356b1d5.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0dd77797-90b3-482b-b27c-f48c06756e86.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0ec22831-585b-49b5-a0f1-a61019c35bcc.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0ef1b8a7-5a38-41de-abf0-b4058df8c7b6.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0e13f1a4-d698-41af-b42a-4c2c84827ed2.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/0ef32d2e-7ea8-4efa-aefc-f1f06947987e.csv.metadata


delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/112195b5-e41c-4858-9ead-57b84bda4e4c.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/1337afe7-aee9-4182-9702-61f782f4ba39.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/11ea7ecb-e24a-4f26-ad1e-8f2c08f8b549.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/1230a452-b928-4036-a29d-c971bda6751b.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/13470bff-2c4a-4b84-8ec1-45660c95fb05.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/134f4dd6-9a6c-48e0-8a68-60cb7e8ec041.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/13507d46-2a15-446b-a6f8-dc1e05118001.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/135385a0-39cf-4e1f-b596-0a810d4f5e5b.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/1381024c-8aa7-4d16-901b-9a4cb539bbd6.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/136fd9b4-2841-4e21-bde4-f539d625afad.csv.metadata


...

ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fcb52f26-bef1-43c4-956a-3b723266cad3.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fd2d5353-a815-4682-940a-f0e868ee3d67.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fd4a11d3-1db0-4063-aeed-588c1af9333a.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fd5ca21e-1fd6-453e-b0bd-645b3bcfd8b6.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fd948182-9103-43c1-9cfc-fe2511519e3c.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fdbe989b-9548-424d-b004-fc4a4fdf03c7.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fbf5a8c8-75f2-4c95-a74f-eed474332320.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fdd59ecb-4fb1-4a5f-94f1-314d0f4f0374.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fdddeaed-50da-452b-b6bc-92762e0e6a92.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fd7d65e5-26a6-4cf9-81fa-72f59ef00373.csv.metadata


ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fe01473d-9532-4a7e-9c38-2f8e5cd85f16.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fd9ed442-9b42-45e0-b5bf-bf3e7ec90891.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fdf19a40-6cf3-44b3-bee8-4539914786c8.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fd863d6e-53cf-4725-a6e6-83637d459050.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fe14a914-eac4-41f1-831f-36d12bd124b2.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fe1711b4-27a0-47f6-8b57-a32b6a7f7349.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fe5181c5-e021-43cc-8471-eb4757961556.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fe277daf-f533-40cb-9690-5a30a0550223.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fe581cb9-3686-44da-81fb-ea295b880a46.csv.metadata
delete: s3://athena-fgv/osm_pems/raw/oms_pems_ids/fea3015a-32b5-4e57-b35c-84ba4db6589d.csv.metadata


ERROR:pyathena.result_set:Failed to fetch result set.
Traceback (most recent call last):
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/result_set.py", line 195, in __fetch
    **request)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/pyathena/util.py", line 44, in retry_api_call
    return retry(func, *args, **kwargs)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 358, in call
    do = self.iter(retry_state=retry_state)
  File "/Users/joaoc/Library/Python/3.6/lib/python/site-packages/tenacity/__init__.py", line 319, in iter
    return fut.result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 398, in result
    return self.__get_result()
  File "/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/concurrent/futures/_base.py", line 357, in __get_result
    raise self._exception
  File "/Users/joaoc/Library/Python/3.6/lib/pyt

# Different try

## Get H3 hexagons that are in the boundary

In [259]:
def boundaries_to_geojson(boundaries):
    
    return {'type': 'Polygon',
 'coordinates': [[[boundaries['max_lat'], boundaries['max_lon']],
                  [boundaries['max_lat'], boundaries['min_lon']],
                  [boundaries['min_lat'], boundaries['min_lon']],
                  [boundaries['min_lat'], boundaries['max_lon']]]] }
    

In [289]:
def hex_coor_to_athena_geo(hex_coor):
    hex_coor = ''.join([str(h).replace(',', '').replace('[', '').replace(']', ',') for h in hex_coor])
    return 'POLYGON(('+ hex_coor[:-2] + '))'

In [290]:
def geojson_to_h3(geojson, res):
    
    return  list(map(lambda x: {'id': x,
                                'res': res,
                                'latitude': h3.h3_to_geo(x)[0],
                                'longitude': h3.h3_to_geo(x)[1],
                                'boundary': h3.h3_to_geo_boundary(x),
                                'boundary_athena': hex_coor_to_athena_geo(h3.h3_to_geo_boundary(x))}, h3.polyfill(geojson, res)))

In [291]:
geojson = boundaries_to_geojson(boundaries)
hexagons_in_region = geojson_to_h3(geojson, 8)

## Write to S3 as parquet

In [310]:
s3_url = 's3://fgv-bd/h3/res=8/calif_3.parquet.gzip'
df = pd.DataFrame(hexagons_in_region).set_index('res')
df.to_parquet(s3_url, compression='gzip')

## Join H3 with OSM

In [147]:
%timeit h3.geo_to_h3(38.50940595263018, -120.3511113181587, 8)

19.4 µs ± 1.6 µs per loop (mean ± std. dev. of 7 runs, 10000 loops each)


In [149]:
osm = pd.read_sql_query("""SELECT id, lat, lon FROM osm.california_district_3 LIMIT 100""", conn)

In [150]:
osm.head()

id        lat         lon
0  1030979464  39.636424 -120.012501
1  1030979570  39.626327 -120.015171
2  1030979605  39.634838 -119.963224
3  1030979617  39.684711 -119.992431
4  1030979762  39.669065 -120.002910

In [154]:
%timeit osm.apply(lambda x: h3.geo_to_h3(x['lat'], x['lon'], 8), axis=1)

18.2 ms ± 1.87 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [159]:
osm = osm.to_dict(orient='record')

In [161]:
%timeit [h3.geo_to_h3(x['lat'], x['lon'], 8) for x in osm]

2.54 ms ± 266 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


# Different Try

Get just hexagons around the sensors


## Get sensors location

In [167]:
query = """
SELECT 
id, MAX(latitude) latitude, MAX(longitude) longitude
FROM pems.pems_station_metadata
GROUP BY id
"""

In [168]:
sensors = pd.read_sql_query(query, conn)

## Get hexagons around sensors

In [169]:
sensors['hexagon_8'] = sensors.apply(lambda x: h3.geo_to_h3(x['latitude'], x['longitude'], 8), axis=1)

In [186]:
len(h3.k_ring('88283284d1fffff', 2))

19

In [191]:
for i in range(7):
    sensors[f'neigh_{i}'] = sensors.apply(lambda x: h3.k_ring(x['hexagon_8'], i), 1)


In [194]:
for i in range(7):
    print('ring: ', i, 'size: ', len(h3.k_ring('88283284d1fffff', i)) * len(sensors))

ring:  0 size:  1341
ring:  1 size:  9387
ring:  2 size:  25479
ring:  3 size:  49617
ring:  4 size:  81801
ring:  5 size:  122031
ring:  6 size:  170307


In [ ]:
## 

In [201]:
sensors['hexagon_8'][0]

'882832b369fffff'

In [195]:
import folium

In [205]:

address = sensors['hexagon_8'][i]
latitude, longitude = sensors['latitude'][i], sensors['longitude'][i]

m = folium.Map(
    location=[latitude, longitude],
    zoom_start=13
)


folium.Polygon(
    h3.h3_to_geo_boundary(sensors['hexagon_8'][0]),
    tooltip=i
).add_to(m)

m

In [247]:
boundari = [h3.h3_to_geo_boundary(sensors['hexagon_8'][0])]

In [250]:
boundaries = {}

In [251]:
a = pd.DataFrame(boundari[0])
boundaries['max_lat'] = a[0].max()
boundaries['min_lat'] = a[0].min()
boundaries['max_lon'] = a[1].max()
boundaries['min_lon'] = a[1].min()

In [237]:
hex_coor_to_athena_geo(boundaries)

'polygon ((38.49158935182575 -121.44559247875796, 38.49509582934222 -121.44102691241622, 38.499783218066796 -121.44244926281223, 38.50096395450605 -121.44843753831455, 38.49745735834504 -121.45300291024557, 38.492770144400396 -121.45158020113382))'

In [254]:
print(f"""WHERE lat < {boundaries['max_lat']}
  AND lat > {boundaries['min_lat']}
  AND lon < {boundaries['max_lon']}
  AND lon > {boundaries['min_lon']}"""

WHERE lat < 38.50096395450605
  AND lat > 38.49158935182575
  AND lon < -121.44102691241622
  AND lon > -121.45300291024557
